In [5]:
import math
import random
import copy
import matplotlib.pyplot as plt
from matplotlib import animation, rc, gridspec
from IPython.display import HTML
import numpy as np

In [6]:
SIZE = 200
MAXX = 100
MAXY = 100
SPEED = [3,2]
HPRATE = [2,5]
LIFESPAN = 50
ADULTAGE = 20
PRODUCEHP = 10
SEARCHSTR = [20,40]

In [7]:
class Agent:
    def __init__(self,name,x,y,speed,hprate,searchstr,age=0):
        self.name = name
        self.x = x
        self.y = y
        self.next_x = 0
        self.next_y = 0
        self.degree = random.randint(1,360)
        self.speed = speed
        self.hprate = hprate
        self.searchstr = searchstr
        self.hp = 30
        self.dechp = 0
        self.age = age
        self.status = 1
        self.find = 0
        self.mated = 0

    def update_xy(self,ally,foods):
        self.find = 0
        if random.random()<0.9:
            self.search(ally,foods)
        if self.find==0:
            self.degree += random.randint(-10,10)
            x_v = math.cos(math.radians(self.degree))*self.speed
            y_v = math.sin(math.radians(self.degree))*self.speed
            self.next_x = self.x + x_v
            self.next_y = self.y + y_v
            if self.next_x<0 or self.next_x>MAXX:
                self.next_x = self.x - x_v
                self.degree += 180
            if self.next_y<0 or self.next_y>MAXY:
                self.next_y = self.y - y_v
                self.degree += 180
        self.x = self.next_x
        self.y = self.next_y

    def update_status(self):
        self.age += 1
        self.hp -= (1+self.dechp)
        self.mated = 0
        if (self.age >= LIFESPAN) | (self.hp <= 0):
            self.status = 0

    def battle(self,enermy):
        self.dechp = 0
        if (self.status == 1):
            for agent in enermy:
                if (agent.status==1) & (abs(self.x-agent.x)<1 ) & (abs(self.y-agent.y)<1):
                    if self.hp > agent.hp:
                        self.dechp += (agent.hp-self.hp)

    def produce(self,ally):
        born = 0
        speed = 0
        hprate = 0
        searchstr = 0
        if (self.mated==0)&(self.hp>PRODUCEHP)&(self.age>=ADULTAGE):
            for agent in ally:
                if (self.name!=agent.name)&(agent.mated==0)&(agent.age>=ADULTAGE)&(agent.hp>=PRODUCEHP):
                    if (abs(self.x-agent.x)<1)&(abs(self.y-agent.y)<1):
                        born += 1
                        if self.hp > agent.hp:
                            speed = self.speed
                            hprate = self.hprate
                            searchstr = self.searchstr
                        else:
                            speed = agent.speed
                            hprate = agent.hprate
                            searchstr = agent.searchstr
                        self.hp -= PRODUCEHP
                        agent.hp -= PRODUCEHP
                        self.mated = 1
                        agent.mated = 1
        return born, speed, hprate, searchstr
    def eat(self,foods):
        for food in foods:
            if food.status == 1:
                if (abs(self.x-food.x)<1)&(abs(self.y-food.y)<1):
                    self.hp += self.hprate
                    food.status = 0
    def search(self,ally,foods):
        if self.age >= ADULTAGE:
            if self.hp < self.searchstr:
                self._search_food(foods)
            else:
                self._search_ally(ally)
    def _search_food(self,foods):
        nearest = 10000
        for food in foods:
            if food.status == 1:
                distance = self._distance(food)
                if distance<nearest:
                    if distance < self.speed:
                        self.find = 1
                        self.next_x = food.x
                        self.next_y = food.y
                    elif distance < self.speed*5:
                        self.find = 1
                        radian = math.atan2(self.y-food.y,self.x-food.x)
                        x_v = math.cos(radian)*self.speed
                        y_v = math.sin(radian)*self.speed
                        self.next_x = self.x - x_v
                        self.next_y = self.y - y_v
                    nearest = distance
    def _search_ally(self,ally):
        nearest = 10000
        for agent in ally:
            if (agent.name != self.name) & (agent.status == 1) & (agent.age >= ADULTAGE):
                distance = self._distance(agent)
                if distance < nearest:
                    if distance < self.speed:
                        self.find = 1
                        self.next_x = self.x + (agent.x - self.x)/2
                        self.next_y = self.y + (agent.y - self.y)/2
                    elif distance < self.speed*3:
                        self.find = 1
                        radian = math.atan2(self.y-agent.y,self.x-agent.x)
                        x_v = math.cos(radian)*self.speed
                        y_v = math.sin(radian)*self.speed
                        self.next_x = self.x - x_v
                        self.next_y = self.y - y_v
                    nearest = distance

    def _distance(self,agent):
        return math.sqrt((self.x-agent.x)**2+(self.y-agent.y)**2)
                
class Food:
    def __init__(self):
        self.x = random.randint(0,MAXX)
        self.y = random.randint(0,MAXY)
        self.status = 1

class Simulation:
    def __init__(self,rate1,rate2):
        self.agents1 = [Agent('1%d'%i,random.randint(0,MAXX),random.randint(0,MAXY),SPEED[0],HPRATE[0],SEARCHSTR[0],age=random.randint(0,LIFESPAN-5)) if random.random()<rate1 else Agent('1',random.randint(0,MAXX),random.randint(0,MAXY),SPEED[1],HPRATE[1],SEARCHSTR[1],age=random.randint(0,LIFESPAN-5)) for i in range(SIZE)]
        self.agents2 = [Agent('2%d'%i,random.randint(0,MAXX),random.randint(0,MAXY),SPEED[0],HPRATE[0],SEARCHSTR[0],age=random.randint(0,LIFESPAN-5)) if random.random()<rate2 else Agent('2',random.randint(0,MAXX),random.randint(0,MAXY),SPEED[1],HPRATE[1],SEARCHSTR[1],age=random.randint(0,LIFESPAN-5)) for i in range(SIZE)]
        self.foods = [Food() for i in range(SIZE*3)]
        self.idx1 = SIZE
        self.idx2 = SIZE
        self.averageage = [0,0]
        self.averagehp = [0,0]

    def update(self,show=False):
        # 別種と会ったらダメージを受ける
        for agent in self.agents1:
            agent.battle(self.agents2)
        for agent in self.agents2:
            agent.battle(self.agents1)

        # 年取ったりHP消耗したり消滅したり
        for agent in self.agents1:
            agent.update_status()
        for agent in self.agents2:
            agent.update_status()
        self.agents1 = [agent for agent in self.agents1 if agent.status==1]
        self.agents2 = [agent for agent in self.agents2 if agent.status==1]
        
        # 食べる
        agents = random.sample(self.agents1+self.agents2,len(self.agents1+self.agents2))
        for agent in agents:
            agent.eat(self.foods)
        self.foods = [food for food in self.foods if food.status==1] + [Food() for i in range(int(SIZE/4))]

        # 繁殖する
        for agent in self.agents1:
            born, speed, hprate, searchstr = agent.produce(self.agents1)
            if born > 0:
                self.idx1 += 1
                self.agents1.append(Agent('1%d'%self.idx1,agent.x,agent.y,speed,hprate,searchstr))
        for agent in self.agents2:
            born, speed, hprate, searchstr = agent.produce(self.agents2)
            if born > 0:
                self.idx2 += 1
                self.agents2.append(Agent('2%d'%self.idx2,agent.x,agent.y,speed,hprate,searchstr))

        # 次の行動をする
        for agent in self.agents1:
            agent.update_xy(self.agents1,self.foods)
        for agent in self.agents2:
            agent.update_xy(self.agents2,self.foods)
        if show==True:
            print(len(self.agents1),len(self.agents2))

In [8]:
sim = Simulation(1,0)

TIMELIMIT =300

fig = plt.figure()
ims = []
for t in range(TIMELIMIT):
    x1 = [sim.agents1[i].x for i in range(len(sim.agents1))]
    y1 = [sim.agents1[i].y for i in range(len(sim.agents1))]
    x2 = [sim.agents2[i].x for i in range(len(sim.agents2))]
    y2 = [sim.agents2[i].y for i in range(len(sim.agents2))]
    x3 = [sim.foods[i].x for i in range(len(sim.foods))]
    y3 = [sim.foods[i].y for i in range(len(sim.foods))]
    im = plt.plot(x1,y1, ".", markersize=12,color='r')
    im += plt.plot(x2,y2, ".", markersize=12,color='b')
    im += plt.plot(x3,y3, "+", markersize=12,color='c')
    ims.append(im)
    if (len(x1)+len(x2)>1500) | (len(x1)+len(x2)<= 0):
        break
    sim.update()

ani = animation.ArtistAnimation(fig, ims, interval=70)
rc("animation", html="jshtml")
plt.close()

ani

In [9]:
ani.save("survival.gif",writer='imagemagick')

MovieWriter imagemagick unavailable; using Pillow instead.
